## Understanding the difference in biomass between high and low NO$_3$ years. 
`Background`: In Notebook `Quartery_biomass_interannual_62_yr.ipynb` I show that the difference in biomass in the summer between high and low NO$_3$ years favors biomass in low NO$_3$ years. 

    - I made sure I plotted this correctly, so now I need to understand why this difference is ocurring 
`Hypothesis`: Under lower NO$_3$ concentrations, small phytoplankton are still not limited, but larger phytoplankton are, so the higher biomass comes from increased small phytoplankton biomass. Where there are higher NO$_3$ concentrations, there would be lower biomass coming from a higher contribution of larger phytoplankton, but lower general phytoplankton biomass?

    - To prove this, I need to understand the general limitation for different phytoplankton groups in low vs high nutrient environemnts. 

    - And also the general contribution of phytoplankton in low vs high nutrient environments

In [1]:
import warnings
warnings.simplefilter("ignore") # Silence warnings
from mpl_toolkits.basemap import Basemap
import matplotlib.pyplot as plt
import numpy as np
import xarray as xr
import numpy as np
from matplotlib.pyplot import figure

import numpy.ma as ma
from netCDF4 import Dataset as NetCDFFile
import glob
import cartopy
import cartopy.crs as ccrs
import pylab 
from copy import deepcopy
import pandas as pd
import matplotlib
import matplotlib.colors as colors
from cartopy.util import add_cyclic_point
plt.rcParams['mathtext.default']='regular'
from collections import OrderedDict
import cmocean
import matplotlib.cm as cm
import matplotlib as mpl
import seaborn as sns
from matplotlib.gridspec import GridSpec
import matplotlib
# Scientific libraries
from numpy import arange,array,ones
from scipy import stats
import os

In [2]:
import re
numbers = re.compile(r'(\d+)')
def numericalSort(value):
    parts = numbers.split(value)
    parts[1::2] = map(int, parts[1::2])
    return parts

### Import interannual dataset [All 63 years of the 2$^{nd}$ cycle]
____ 

In [3]:
path = '/glade/campaign/cesm/development/bgcwg/projects/marbl-spectra/g.e21.G1850ECOIAF.t62_g17.marbl0_33.GNG595/ocn/hist'
case = 'g.e21.G1850ECOIAF.t62_g17.marbl0_33.GNG595.pop.h.'

In [4]:
variables = ['mp1_P_lim_Cweight_avg_100m','mp1_Fe_lim_Cweight_avg_100m','mp1_N_lim_Cweight_avg_100m', 'mp1_light_lim_Cweight_avg_100m','TEMP', 'mp1_light_lim_surf']
coords = {'x':'TLONG','y':'TLAT'}
keep_vars = variables + list(coords.values())+['dz','KMT','time']

In [5]:
yr = ['062','063','064','065','066','067','068','069',
     '070','071','072','073','074','075','076','077',
     '078','079','080','081','082','083','084','085',
     '086','087','088','089','090','091','092','093',
     '094','095','096','097','098','099','100','101',
     '102','103','104','105','106','107','108','109',
     '110','111','112','113','114','115','116','117',
     '118','119','120','121','122','123','124']

In [6]:
%%time

ds_ann = xr.Dataset()

for year in np.arange(0,63,1):
    yr4=yr[year]
    print(yr4)
    
    ds = xr.Dataset()
    file = sorted(glob.glob(f'{path}/{case}0{yr4}*.nc'))
    dsv=xr.open_mfdataset(file, decode_times=True,drop_variables=["transport_components", "transport_regions"], 
                            parallel=True, compat="override", combine='nested', concat_dim="time",data_vars="minimal",coords='minimal' )
    for vv in variables: 
        #print('got dsv')
        ds = xr.merge((ds, dsv[vv]))   

    ds = ds.drop([v for v in ds.variables if v not in keep_vars]).squeeze()
    #print('monthly file', len(ds.time))
    #ds = ds.mean(dim='time')
    ds_ann = xr.concat([ds_ann, ds], dim="year",data_vars="different",join="override")

062
063
064
065
066
067
068
069
070
071
072
073
074
075
076
077
078
079
080
081
082
083
084
085
086
087
088
089
090
091
092
093
094
095
096
097
098
099
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
CPU times: user 9min 51s, sys: 1min 17s, total: 11min 9s
Wall time: 12min 31s


#### Picoplankton nutrient limitation 

In [7]:
mp1_lims=np.stack([ds_ann.mp1_P_lim_Cweight_avg_100m,
                   ds_ann.mp1_Fe_lim_Cweight_avg_100m,
                   ds_ann.mp1_N_lim_Cweight_avg_100m],axis=4)

mp1_lims_value=np.zeros(shape=ds_ann.mp1_light_lim_Cweight_avg_100m.shape)
mp1_lims_index=np.zeros(shape=ds_ann.mp1_light_lim_Cweight_avg_100m.shape)

for i,t in enumerate(ds_ann.year.values):
        temp=mp1_lims[i,:,:,:]
        mp1_lims_value[i,:,:]=deepcopy(np.amin(temp,axis=3))
        mp1_lims_index[i,:,:]=deepcopy(np.argmin(temp,axis=3))
        
ds_ann['mp1_lims_value']=xr.DataArray(data=mp1_lims_value, coords={'year':ds_ann.year.values}, dims=['year','time','nlat','nlon'], 
                                 attrs={'long_name':'diatom 1 maximum limitation value, carbon biomass weighted average over 0-100m'})
ds_ann['mp1_lims_index']=xr.DataArray(data=mp1_lims_index, coords={'year':ds_ann.year.values}, dims=['year','time','nlat','nlon'], 
                                 attrs={'long_name':'diatom 1 maximum limitation type, carbon biomass weighted average over 0-100m',
                                        'values':'0-light,1-temp, 2-P, 3-Fe, 4-N, 5-Si'})

### Now find the most limiting factor using the light and temperature values
____

### Calcualte the temperature limiation term! 
$$r = r_o e^{\frac{-E_a(T_o -T)}{k T_o T}}$$
$$\frac{\mu}{\mu_o} = e^{\frac{-E_a(T_o -T)}{k T_o T}}$$ 

to simplify however, we will create $\alpha = \frac{E_a}{k}$ and $\gamma_T = 
\frac{\mu}{\mu_o}$ so that: 
$$\gamma_T = e^{ \frac{-\alpha(T_o - T)}{T_o T}}$$

$T_o = 298.15 ^oK$
* it is close to the temperature at which many physiological experiments are run, and it is the mean temperature of the subtropical gyres, which represent a large proportion of the world’s open oceans.

$k = 8.617e^{-5} eVK^{-1}$ 

$E_a = 0.317$ phytoplankton (Kremer et al., 2017).

$E_a = 0.42$ picoplankton 
* Multiple studies have shown that picoplankton have a higher temperature sensitivity compared to phytoplankton of larger sizes (Chen et al., 2014; Stawiarski et al., 2016).

$E_a = 0.65$ zooplankton 
* MTE predicts that heterotrophic organisms will have a greater temperature dependence than autotrophs, as Rubisco carboxylation (rate limiting for photosynthesis) has a lower activation energy (Ea) than ATP synthesis (Allen et al., 2005; Lopez-Urrutia et al., 2006).

and we will have to convert all the surface temperatures from $^oC$ to $K$ and the temperature on the equation and then solve for every gorup... 
$$0°C + 273.15 = 273.15K$$

In [8]:
# convert celcius to kelvin 
temp_K = ds_ann.TEMP + 273.15

# constants 
𝑘=8.617e-5
𝐸𝑎_phyto = 0.317 
𝐸𝑎_pico  = 0.42
𝐸𝑎_zoo   = 0.65
𝑇𝑜 = 298.15

# create simpler variables. 
𝛼_phyto = 𝐸𝑎_phyto/𝑘
𝛼_pico = 𝐸𝑎_pico/𝑘

# calculate temperature limitation term
𝛾𝑇_phyto = np.exp((-𝛼_phyto*(𝑇𝑜-temp_K))/(𝑇𝑜*temp_K))
𝛾𝑇_pico = np.exp((-𝛼_pico*(𝑇𝑜-temp_K))/(𝑇𝑜*temp_K))

In [9]:
ds_ann

<xarray.Dataset>
Dimensions:                         (time: 12, year: 63, nlat: 384, nlon: 320, z_t: 60)
Coordinates:
  * time                            (time) object 0062-02-01 00:00:00 ... 006...
  * year                            (year) int64 0 1 2 3 4 5 ... 58 59 60 61 62
    TLONG                           (nlat, nlon) float64 320.6 321.7 ... 319.8
    TLAT                            (nlat, nlon) float64 -79.22 -79.22 ... 72.19
Dimensions without coordinates: nlat, nlon, z_t
Data variables:
    mp1_light_lim_Cweight_avg_100m  (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_light_lim_surf              (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_N_lim_Cweight_avg_100m      (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_P_lim_Cweight_avg_100m      (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_Fe_lim_Cweight_avg_100m     (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    TEMP                            (year, time, z_t, nlat, nlon) float32 dask.array<chunksize=(2, 1, 60, 128, 80), meta=np.ndarray>
    mp1_lims_value                  (year, time, nlat, nlon) float64 nan ... nan
    mp1_lims_index                  (year, time, nlat, nlon) float64 0.0 ... 0.0

In [10]:
mp1_lim = np.stack([ds_ann.mp1_light_lim_surf, 
                       𝛾𝑇_phyto[:,:,0,:,:], ds_ann.mp1_lims_value],axis=4)

#### Picoplankton growth limitation 

In [11]:
mp1_lim_value=np.zeros(shape=ds_ann.mp1_light_lim_Cweight_avg_100m.shape)
mp1_lim_index=np.zeros(shape=ds_ann.mp1_light_lim_Cweight_avg_100m.shape)

for i,t in enumerate(ds_ann.year.values):
        temp=mp1_lim[i,:,:,:,:]
        mp1_lim_value[i,:,:,:]=deepcopy(np.amin(temp,axis=3))
        mp1_lim_index[i,:,:,:]=deepcopy(np.argmin(temp,axis=3))
        
ds_ann['mp1_lim_value']=xr.DataArray(data=mp1_lim_value, coords={'year':ds_ann.year.values}, dims=['year','time','nlat','nlon'], 
                                 attrs={'long_name':'mixed phytoplankton 1 maximum limitation value, carbon biomass weighted average over 0-100m'})
ds_ann['mp1_lim_index']=xr.DataArray(data=mp1_lim_index, coords={'year':ds_ann.year.values}, dims=['year','time','nlat','nlon'], 
                                 attrs={'long_name':'mixed phytoplankton 1 maximum limitation type, carbon biomass weighted average over 0-100m',
                                        'values':'0-light,1-temp, 2-Nutrient'})

In [14]:
ds_ann

<xarray.Dataset>
Dimensions:                         (time: 12, year: 63, nlat: 384, nlon: 320, z_t: 60)
Coordinates:
  * time                            (time) object 0062-02-01 00:00:00 ... 006...
  * year                            (year) int64 0 1 2 3 4 5 ... 58 59 60 61 62
    TLONG                           (nlat, nlon) float64 320.6 321.7 ... 319.8
    TLAT                            (nlat, nlon) float64 -79.22 -79.22 ... 72.19
Dimensions without coordinates: nlat, nlon, z_t
Data variables:
    mp1_light_lim_Cweight_avg_100m  (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_light_lim_surf              (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_N_lim_Cweight_avg_100m      (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_P_lim_Cweight_avg_100m      (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    mp1_Fe_lim_Cweight_avg_100m     (year, time, nlat, nlon) float32 dask.array<chunksize=(2, 1, 384, 320), meta=np.ndarray>
    TEMP                            (year, time, z_t, nlat, nlon) float32 dask.array<chunksize=(2, 1, 60, 128, 80), meta=np.ndarray>
    mp1_lims_value                  (year, time, nlat, nlon) float64 nan ... nan
    mp1_lims_index                  (year, time, nlat, nlon) float64 0.0 ... 0.0
    mp1_lim_value                   (year, time, nlat, nlon) float64 nan ... nan
    mp1_lim_index                   (year, time, nlat, nlon) float64 0.0 ... 0.0

In [ ]:
new_filename_1 = '/glade/u/home/gabyn/scratch/SPECTRA/growth_lim/mp1_limitation.nc'
ds_ann.to_netcdf(path=new_filename_1)

	NC4_create: path /glade/u/home/gabyn/scratch/SPECTRA/growth_lim/mp1_limitation.nc cmode 0x1000 parameters (nil)
	HDF5 error messages turned on.
			nc4_create_file: path /glade/u/home/gabyn/scratch/SPECTRA/growth_lim/mp1_limitation.nc mode 0x1000
			nc4_grp_list_add: name / 
		nc_inq_format: ncid 0x10000
		NC4_inq_format_extended: ncid 0x10000
		nc_inq_typeids: ncid 0x10000
		NC4_inq: ncid 0x10000
		NC4_inq: ncid 0x10000
		nc_inq_grps: ncid 0x10000
		NC4_def_dim: ncid 0x10000 name time len 12
		NC4_def_dim: ncid 0x10000 name year len 63
		NC4_def_dim: ncid 0x10000 name nlat len 384
		NC4_def_dim: ncid 0x10000 name nlon len 320
		NC4_def_dim: ncid 0x10000 name z_t len 60
		NC4_def_var: name time type 10 ndims 1
		NC4_inq_unlimdims: ncid 0x10000
		NC4_inq_var_all: ncid 0x10000 varid 0
		NC4_inq_var_all: ncid 0x10000 varid 0
		nc_inq_format: ncid 0x10000
	nc4_put_att: ncid 0x10000 varid 0 name units file_type 2 mem_type 2 len 37
	nc4_put_att: ncid 0x10000 varid 0 name units file_type 2 me

In [ ]:
from matplotlib.colors import LinearSegmentedColormap
colors = [(0.9994925028835063, 0.9192618223760093, 0.6061361014994233),(0.45066769191336664, 0.7509983339741125, 0.7703857490708702),(0.6825187635707243, 0.810691907283208, 0.6352470180118206)]

cmap_name = 'my_list'
cm = LinearSegmentedColormap.from_list(
        cmap_name, colors, N=3)

## Now that I have saved it into a new netCDF, I will regrid this nc file to be able to use it for this figure. I will do this by: 
    - module load nco 
    - module load cdo 

`ncatted -a coordinates,pp_lim_index,c,c,"TLONG TLAT" pp_lim_ds.nc`

`ncatted -a coordinates,pp_lim_value,c,c,"TLONG TLAT" pp_lim_ds.nc`

`cdo remapbil,r360x180 -selname,pp_lim_index pp_lim_ds.nc pp_lim_index_remap.nc`

`cdo remapbil,r360x180 -selname,pp_lim_value pp_lim_ds.nc pp_lim_value_remap.nc`

`cdo sellonlatbox,-180,180,-89.5,89.5 pp_lim_index_remap.nc regrid_pp_lim_index.nc`

`cdo sellonlatbox,-180,180,-89.5,89.5 pp_lim_value_remap.nc regrid_pp_lim_value.nc`

In [ ]:
# Diatom 
ncatted -a coordinates,diat1_lim_index,c,c,"TLONG TLAT" diat1_limitation.nc
ncatted -a coordinates,diat1_lim_value,c,c,"TLONG TLAT" diat1_limitation.nc

cdo remapbil,r360x180 -selname,diat1_lim_index diat1_limitation.nc diat1_limitation_index.nc
cdo remapbil,r360x180 -selname,diat1_lim_value diat1_limitation.nc diat1_limitation_value.nc

cdo sellonlatbox,-180,180,-89.5,89.5 diat1_limitation_index.nc regrid_diat1_limitation_index.nc
cdo sellonlatbox,-180,180,-89.5,89.5 diat1_limitation_value.nc regrid_diat1_limitation_value.nc


# Mixed phytoplankton 
ncatted -a coordinates,mp1_lim_index,c,c,"TLONG TLAT" mp1_limitation.nc
ncatted -a coordinates,mp1_lim_value,c,c,"TLONG TLAT" mp1_limitation.nc

cdo remapbil,r360x180 -selname,mp1_lim_index mp1_limitation.nc mp1_limitation_index.nc
cdo remapbil,r360x180 -selname,mp1_lim_value mp1_limitation.nc mp1_limitation_value.nc

cdo sellonlatbox,-180,180,-89.5,89.5 mp1_limitation_index.nc regrid_mp1_limitation_index.nc
cdo sellonlatbox,-180,180,-89.5,89.5 mp1_limitation_value.nc regrid_mp1_limitation_value.nc

# Picoplankton 
ncatted -a coordinates,pp_lim_index,c,c,"TLONG TLAT" pp_limitation.nc
ncatted -a coordinates,pp_lim_value,c,c,"TLONG TLAT" pp_limitation.nc

cdo remapbil,r360x180 -selname,pp_lim_index pp_limitation.nc pp_limitation_index.nc
cdo remapbil,r360x180 -selname,pp_lim_value pp_limitation.nc pp_limitation_value.nc

cdo sellonlatbox,-180,180,-89.5,89.5 pp_limitation_index.nc regrid_pp_limitation_index.nc
cdo sellonlatbox,-180,180,-89.5,89.5 pp_limitation_value.nc regrid_pp_limitation_value.nc